# QAOA Portfolio Optimization with Parallel Multi-Start Optimization and Pre-Transpiled Circuits (DWE)

This notebook implements a **Parallel Multi-Start Optimization** strategy for QAOA parameters in portfolio optimization, using Domain Wall Encoding (DWE) for the constraint handling.

The key optimization in this version is that the quantum circuit for QAOA is **built and transpiled only once per parallel optimization run**, instead of once per cost function evaluation. This significantly reduces overhead and improves performance for classical optimizers that make many calls to the objective function.

**To address the `AttributeError` with `multiprocessing` in Jupyter, the core helper functions (`_calculate_energy_from_counts`, `get_qaoa_portfolio_objective_optimized`, `run_single_optimization_optimized`) are now defined in a separate file `qaoa_helpers.py` and imported.**

**Key components:**
- **Optimized QAOA Objective:** A function `get_qaoa_portfolio_objective_optimized` (imported) that handles the one-time circuit building and transpilation.
- **Optimized Worker Function:** A function `run_single_optimization_optimized` (imported) that utilizes the optimized objective within each parallel run.
- **`multiprocessing.Pool`**: Used to manage and execute the `run_single_optimization_optimized` calls in parallel across available CPU cores.

## 1. Setup and Imports

We'll import necessary libraries, including `multiprocessing` for parallel processing and Qiskit components.

In [6]:
import os
import json
import numpy as np
import time
import logging
import itertools
import pandas as pd
import multiprocessing

# --- Setup Master Logger for the main notebook process ---
main_logger = logging.getLogger("BenchmarkMain")
if not main_logger.handlers:
    main_handler = logging.StreamHandler()
    formatter = logging.Formatter('%(asctime)s - %(name)s - %(levelname)s - %(message)s')
    main_handler.setFormatter(formatter)
    main_logger.addHandler(main_handler)
    main_logger.setLevel(logging.INFO) # Set to INFO for main process
    main_logger.propagate = False

main_logger.info("Notebook Cell 1: Setup complete.")

# --- Qiskit Backend Import ---
# Assuming you have qiskit_aer installed: pip install qiskit-aer
from qiskit_aer import AerSimulator

2025-06-13 15:44:34,000 - BenchmarkMain - INFO - Notebook Cell 1: Setup complete.


## 2. Define Problem Parameters (with DWE) & Benchmarking Setup

This section defines your portfolio optimization problem with DWE. For benchmarking, it will loop through different internal thread configurations for `os.environ` variables, running a single QAOA optimization for each.

It also performs a classical brute-force calculation for smaller `N` for comparison, if applicable.

In [7]:
import sys
# Add the path to your QOKit project so Python can find its modules
qokit_path = '/Users/abdulmalekbaitulmal/PycharmProjects/QOKit'
if qokit_path not in sys.path:
    sys.path.insert(0, qokit_path)

# Import necessary QOKit modules
try:
    # While you're defining a custom problem, get_problem might still be needed for other utilities
    from qokit.portfolio_optimization import get_problem # Keep this if you use it elsewhere
    # And potentially get_parameterized_qaoa_circuit for the visualization later in this cell
    from qokit.qaoa_circuit_portfolio import get_parameterized_qaoa_circuit
    main_logger.info("Successfully imported necessary QOKit modules.")
except ImportError as e:
    main_logger.error(f"Error importing QOKit modules: {e}. Make sure QOKit is installed or its path is correct.")
    raise

# --- For Circuit Visualization (if needed) ---
import matplotlib.pyplot as plt
from qiskit_aer import AerSimulator # Already imported in Cell 1, but useful context here
from qiskit import transpile # Already imported in qaoa_circuit_portfolio.py

# --- Define Problem Parameters (aligned with your DWE notebook) ---
N = 22 # Your chosen N for this benchmark
K = int(N * 0.4) # K is now derived from N
p = 1 # Number of QAOA layers (depth)
max_iterations_optimizer = 50 # Max iterations for the classical optimizer
num_shots_simulator = 256 # Number of shots for quantum circuit simulation
q = 0.5 # Risk aversion parameter
lambda_sum = 0 # DWE-inspired penalty coefficient for sum constraint
mixer_topology = 'ring' # Corrected based on your specific 'trotter_ring' usage in qaoa_circuit_portfolio.py

# --- Generate random mu and Sigma for larger N ---
np.random.seed(42) # for reproducibility of the problem definition
mu = np.random.uniform(0.05, 0.20, N)
Sigma = np.random.uniform(0.001, 0.015, (N, N))
Sigma = (Sigma + Sigma.T) / 2 # Make it symmetric
Sigma = Sigma + np.eye(N) * 0.005 # Add a small diagonal component for stability

# --- Calculate Coefficients for Total Cost Hamiltonian (H_C = H_C^objective + H_C^DWE-penalty) ---
factor_J_obj = (2 * q) / (K**2)
factor_h_linear_obj = -1 / K
factor_h_diagonal_obj = q / (K**2)

J_coeffs_objective = {}
h_coeffs_objective = {}

for i in range(N):
    for j in range(i + 1, N):
        J_coeffs_objective[(i, j)] = factor_J_obj * Sigma[i, j]

for i in range(N):
    h_coeffs_objective[i] = factor_h_linear_obj * mu[i] + factor_h_diagonal_obj * Sigma[i, i]

J_coeffs_total = {}
h_coeffs_total = {}

# Deep copy objective coefficients as a starting point
for (i, j), val in J_coeffs_objective.items():
    J_coeffs_total[(i, j)] = val

for i, val in h_coeffs_objective.items():
    h_coeffs_total[i] = val

# Add DWE penalty coefficients
for i in range(N):
    for j in range(i + 1, N):
        # The DWE penalty term for the quadratic part is lambda_sum * Z_i * Z_j.
        # When converting to QUBO (with x_i = (Z_i + 1)/2 => Z_i = 2x_i - 1),
        # Z_i Z_j becomes (2x_i - 1)(2x_j - 1) = 4x_i x_j - 2x_i - 2x_j + 1.
        # So, the coefficient of 4x_i x_j maps to 4 * J_ij in the standard QUBO-to-Ising mapping.
        # If the DWE penalty is added to J_ij, it should be added to the original J_ij terms.
        # If lambda_sum is small, this might not be a large effect.
        # Let's assume the previous logic for J_coeffs_total and h_coeffs_total directly adds the penalty.
        # Your original code added `+ 2 * lambda_sum` to J_coeffs_total, and `- 5 * lambda_sum` to h_coeffs_total.
        # This implies a specific QUBO penalty translation. Sticking with your original.
        J_coeffs_total[(i, j)] += 2 * lambda_sum # Corrected based on your provided block

for i in range(N):
    h_coeffs_total[i] -= 5 * lambda_sum # Corrected based on your provided block

# Construct the custom po_problem dictionary with DWE coefficients
po_problem_for_worker = { # Renamed to match the variable used in Cell 3
    "N": N,
    "K": K,
    "q": q,
    "J": J_coeffs_total,
    "h": h_coeffs_total,
    "means": mu.tolist(),
    "cov": Sigma.tolist(),
    "q_orig": q,
    "scale": 1.0 # This is often 1.0 if not scaling the objective
}

main_logger.info(f"--- Problem Parameters & Custom QUBO Defined for N={N} ---")
main_logger.info(f"Number of assets (N): {N}")
main_logger.info(f"Assets to select (K): {K}")
main_logger.info(f"QAOA Layers (p): {p}")
main_logger.info(f"DWE Penalty Lambda_sum: {lambda_sum}")
main_logger.info(f"Optimizer Max Iterations: {max_iterations_optimizer}")
main_logger.info(f"Simulator Shots: {num_shots_simulator}")
main_logger.info(f"Mixer Topology: {mixer_topology}")


# --- Display Calculated QUBO Coefficients ---
main_logger.info("\n--- Calculated QUBO Coefficients ---")
main_logger.info("\nObjective Hamiltonian (H_C^objective) Coefficients:")
# Use json.dumps to pretty print dictionaries, converting tuple/int keys to strings for JSON
main_logger.info("  J_obj (Quadratic Terms):")
main_logger.info(json.dumps({str(k): f"{v:.6f}" for k, v in J_coeffs_objective.items()}, indent=2)[:500] + "...")
main_logger.info("  h_obj (Linear Terms):")
main_logger.info(json.dumps({str(k): f"{v:.6f}" for k, v in h_coeffs_objective.items()}, indent=2))

main_logger.info("\nFull Cost Hamiltonian (H_C = H_C^objective + H_C^DWE-penalty) Coefficients:")
main_logger.info("  J_total (Quadratic Terms):")
main_logger.info(json.dumps({str(k): f"{v:.6f}" for k, v in J_coeffs_total.items()}, indent=2)[:500] + "...")
main_logger.info("  h_total (Linear Terms):")
main_logger.info(json.dumps({str(k): f"{v:.6f}" for k, v in h_coeffs_total.items()}, indent=2))
main_logger.info("-" * 50)


# --- Handle best_portfolio (from brute-force) ---
best_portfolio = (None, None) # E_min, E_max
if N <= 20:
    try:
        from qokit.portfolio_optimization import portfolio_brute_force
        main_logger.info("Calculating classical brute-force solution (may take time for N up to 20)....")
        original_po_problem_for_brute_force = {
            "N":N, "K":K, "q":q, "means":mu, "cov":Sigma, "scale": 1.0
        }
        best_portfolio = portfolio_brute_force(original_po_problem_for_brute_force, return_bitstring=False)
        main_logger.info(f"Brute-force classical optimal energy (E_min): {best_portfolio[0]:.6f}")
        main_logger.info(f"Brute-force classical worst energy (E_max): {best_portfolio[1]:.6f}")
    except ImportError:
        main_logger.warning("qokit.portfolio_optimization.portfolio_brute_force not available or failed.")
        main_logger.warning("Approximation Ratio will not be calculated.")
    except Exception as e:
        main_logger.error(f"Brute-force calculation failed: {e}")
        main_logger.warning("Approximation Ratio will not be calculated.")
else:
    main_logger.info(f"Brute-force calculation is not feasible for N = {N} > 20. Approximation Ratio will not be calculated.")

main_logger.info("-" * 50)


# --- Example QAOA Circuit Visualization and Gate Operations ---
main_logger.info("\n--- Example QAOA Circuit and Gate Operations ---")
# Use dummy parameters for visualization (e.g., all zeros)
dummy_gammas = np.zeros(p)
dummy_betas = np.zeros(p)

# Ensure get_parameterized_qaoa_circuit is called with mixer_topology
example_circuit, _, _ = get_parameterized_qaoa_circuit(
    po_problem=po_problem_for_worker, # Use the correct problem dictionary
    depth=p,
    ini_type='dicke', # Match your chosen ini_type
    mixer_type='trotter_ring', # Match your chosen mixer_type
    mixer_topology=mixer_topology, # Pass the mixer_topology
    gamma_params=None, # These will be created internally
    beta_params=None   # These will be created internally
)
example_circuit.measure_all() # Add measurements for a complete circuit representation

main_logger.info(f"\nLogical Circuit (before transpilation):")
main_logger.info(f"  Circuit depth: {example_circuit.depth()}")
main_logger.info(f"  Number of qubits: {example_circuit.num_qubits}")
main_logger.info("  Gate counts (logical gates):")
main_logger.info(example_circuit.count_ops())

# Transpile the circuit for a generic simulator to see how it would look on a real backend
temp_simulator = AerSimulator()
transpiled_example_circuit = transpile(example_circuit, temp_simulator, optimization_level=0) # opt_level 0 for direct mapping

main_logger.info(f"\nTranspiled Circuit (optimization_level=0):")
main_logger.info(f"  Transpiled circuit depth: {transpiled_example_circuit.depth()}")
main_logger.info(f"  Transpiled gate counts:")
main_logger.info(transpiled_example_circuit.count_ops())

# Draw the circuit (will be displayed inline in Jupyter)
main_logger.info("\nVisualizing an Example QAOA Circuit (with dummy parameters and measurements):")
%matplotlib inline
fig = example_circuit.draw(output='mpl', style={'fontsize': 8, 'linecolor': '#000000'}, fold=100)
plt.tight_layout()
plt.show(fig)

main_logger.info("-" * 50)

# The po_problem_for_worker is now defined and ready for use in Cell 3.
main_logger.info("Notebook Cell 2: Custom problem definition and QAOA parameters set up.")

2025-06-13 15:44:34,032 - BenchmarkMain - INFO - Successfully imported necessary QOKit modules.
2025-06-13 15:44:34,034 - BenchmarkMain - INFO - --- Problem Parameters & Custom QUBO Defined for N=22 ---
2025-06-13 15:44:34,035 - BenchmarkMain - INFO - Number of assets (N): 22
2025-06-13 15:44:34,035 - BenchmarkMain - INFO - Assets to select (K): 8
2025-06-13 15:44:34,036 - BenchmarkMain - INFO - QAOA Layers (p): 1
2025-06-13 15:44:34,036 - BenchmarkMain - INFO - DWE Penalty Lambda_sum: 0
2025-06-13 15:44:34,036 - BenchmarkMain - INFO - Optimizer Max Iterations: 50
2025-06-13 15:44:34,036 - BenchmarkMain - INFO - Simulator Shots: 256
2025-06-13 15:44:34,036 - BenchmarkMain - INFO - Mixer Topology: ring
2025-06-13 15:44:34,037 - BenchmarkMain - INFO - 
--- Calculated QUBO Coefficients ---
2025-06-13 15:44:34,037 - BenchmarkMain - INFO - 
Objective Hamiltonian (H_C^objective) Coefficients:
2025-06-13 15:44:34,037 - BenchmarkMain - INFO -   J_obj (Quadratic Terms):
2025-06-13 15:44:34,038 

2025-06-13 15:44:50,221 - BenchmarkMain - INFO - --------------------------------------------------
2025-06-13 15:44:50,224 - BenchmarkMain - INFO - Notebook Cell 2: Custom problem definition and QAOA parameters set up.


## 3. Optimized QAOA Objective Function and Parallel Worker Function (Imported from `qaoa_helpers.py`)

These functions are now imported from the `qaoa_helpers.py` file to ensure proper pickling for multiprocessing.

In [8]:
import os
import json
import numpy as np
import time
import logging
import itertools
import pandas as pd
import multiprocessing

# Import the worker functions from the separate file
from qaoa_workers import worker_init, run_single_optimization_optimized

# --- Master Logger Setup (for the main notebook process) ---
main_logger = logging.getLogger("BenchmarkMain")
if not main_logger.handlers:
    main_handler = logging.StreamHandler()
    formatter = logging.Formatter('%(asctime)s - %(name)s - %(levelname)s - %(message)s')
    main_handler.setFormatter(formatter)
    main_logger.addHandler(main_handler)
    main_logger.setLevel(logging.INFO)
    main_logger.propagate = False

# --- Qiskit Backend Import ---
from qiskit_aer import AerSimulator

# --- Confirm problem parameters are loaded from Cell 2 ---
main_logger.info(f"Main process: Using QAOA parameters: N={N}, K={K}, p={p}.")
main_logger.info(f"Main process: Loaded problem data (keys): {po_problem_for_worker.keys()}.")

# --- Define the logging level for worker processes ---
logging_level_workers = logging.INFO

# --- Define the thread counts to test for each environment variable ---
thread_values = [1, 4, 8]

# --- Define the environment variables we want to test combinations for ---
env_vars_to_test = {
    "OMP_NUM_THREADS": thread_values,
    "OPENBLAS_NUM_THREADS": thread_values,
    "MKL_NUM_THREADS": thread_values,
    "VECLIB_MAXIMUM_THREADS": thread_values,
    "NUMEXPR_NUM_THREADS": thread_values,
}

# --- Generate all combinations of thread counts ---
all_combinations = list(itertools.product(*env_vars_to_test.values()))

# --- Storage for benchmark results ---
benchmark_results_list = []

# --- Main execution block for multiprocessing ---
if __name__ == '__main__':
    try:
        multiprocessing.set_start_method('spawn', force=True)
        main_logger.info("Multiprocessing start method set to 'spawn'.")
    except RuntimeError as e:
        main_logger.warning(f"Could not set start method: {e}. It might already be set or not supported.")


    main_logger.info(f"--- Starting Comprehensive Benchmarking for N={N} (Combinatorial Internal Threading) ---")
    main_logger.info(f"Total combinations to test: {len(all_combinations)}")
    main_logger.info(f"Estimated time: {len(all_combinations)} runs. Please be patient, this will take a while.")

    simulator_type_for_qokit = 'qiskit'
    simulator_backend_obj = AerSimulator()

    run_counter = 0
    for combo in all_combinations:
        run_counter += 1

        current_env_settings = dict(zip(env_vars_to_test.keys(), combo))

        main_logger.info(f"\n{'='*80}")
        main_logger.info(f"===== Run {run_counter}/{len(all_combinations)}: Testing with settings: {current_env_settings} =====")
        main_logger.info(f"{'='*80}")

        for var, val in current_env_settings.items():
            os.environ[var] = str(val)
            main_logger.info(f"  {var}: {os.environ.get(var)}")
        main_logger.info("\n")

        current_num_parallel_Proc = 1

        main_logger.info(f"Starting 1 QAOA optimization run with p={p} (internal threads controlled by env vars)...")

        run_start_time_total = time.perf_counter()

        worker_args = (
            run_counter,
            po_problem_for_worker,
            p,
            None, # initial_point_override, still None
            'dicke', # <--- CHANGE THIS TO 'dicke'
            'trotter_ring',
            1,
            simulator_type_for_qokit,
            num_shots_simulator,
            simulator_backend_obj,
            None,
            'COBYLA',
            None,
            current_env_settings,
            max_iterations_optimizer,
            mixer_topology
        )

        result = None
        try:
            with multiprocessing.Pool(processes=current_num_parallel_Proc,
                                      initializer=worker_init,
                                      initargs=(logging_level_workers,)) as pool:
                results_future = pool.apply_async(run_single_optimization_optimized, worker_args)
                result = results_future.get(timeout=3600)
        except multiprocessing.TimeoutError:
            main_logger.error(f"Run {run_counter} timed out after 3600 seconds. Settings: {current_env_settings}")
            result = {"success": False, "energy": float('inf'), "nfev": -1, "optimizer_time": -1, "run_id": run_counter, "initial_point_strategy": 'dicke', "optimizer_method": 'COBYLA', "N_qubits": N, "p_value": p, "env_vars": current_env_settings}
        except Exception as e:
            main_logger.error(f"ERROR: Multiprocessing Pool creation or execution failed for run {run_counter}: {e}", exc_info=True)
            result = {"success": False, "energy": float('inf'), "nfev": -1, "optimizer_time": -1, "run_id": run_counter, "initial_point_strategy": 'dicke', "optimizer_method": 'COBYLA', "N_qubits": N, "p_value": p, "env_vars": current_env_settings}

        run_end_time_total = time.perf_counter()
        total_duration_overall = run_end_time_total - run_start_time_total

        main_logger.info(f"Run {run_counter}: Optimization finished. Success: {result['success']}, Energy: {result['energy']:.6f}, NFEV={result['nfev']}, Opt Time={result['optimizer_time']:.2f}s")
        main_logger.info(f"Total overall duration for this combination: {total_duration_overall:.2f} seconds.")

        entry = {
            "run_id": run_counter,
            "total_overall_duration": total_duration_overall,
            "optimizer_runtime": result['optimizer_time'],
            "nfev": result['nfev'],
            "optimal_energy": result['energy'],
            "success": result['success']
        }
        entry.update(current_env_settings)
        benchmark_results_list.append(entry)

        main_logger.info(f"{'='*80}")

    df_results = pd.DataFrame(benchmark_results_list)

    main_logger.info("\n\n" + "#"*80)
    main_logger.info("### COMPREHENSIVE INTERNAL THREADING BENCHMARKING SUMMARY ###")
    main_logger.info("#"*80)
    main_logger.info(f"Problem N={N}, K={K}, p={p}, Max Iterations={max_iterations_optimizer}")
    main_logger.info("\nResults DataFrame:")
    main_logger.info(df_results.to_string())

    main_logger.info("\n--- Next Steps ---")
    main_logger.info("Now you have the data in 'df_results' DataFrame. Use matplotlib/seaborn to visualize.")
    main_logger.info("Consider plotting 'optimizer_runtime' and 'total_overall_duration' against combinations of parameters.")
    main_logger.info("For many combinations, scatter plots or heatmaps (if you fix some variables) will be more effective than bar charts.")
    main_logger.info("--------------------------------------------------------------------------------")

2025-06-13 15:44:51,687 - BenchmarkMain - INFO - Main process: Using QAOA parameters: N=22, K=8, p=1.
2025-06-13 15:44:51,687 - BenchmarkMain - INFO - Main process: Loaded problem data (keys): dict_keys(['N', 'K', 'q', 'J', 'h', 'means', 'cov', 'q_orig', 'scale']).
2025-06-13 15:44:51,688 - BenchmarkMain - INFO - Multiprocessing start method set to 'spawn'.
2025-06-13 15:44:51,688 - BenchmarkMain - INFO - --- Starting Comprehensive Benchmarking for N=22 (Combinatorial Internal Threading) ---
2025-06-13 15:44:51,688 - BenchmarkMain - INFO - Total combinations to test: 243
2025-06-13 15:44:51,689 - BenchmarkMain - INFO - Estimated time: 243 runs. Please be patient, this will take a while.
2025-06-13 15:44:51,689 - BenchmarkMain - INFO - 
2025-06-13 15:44:51,690 - BenchmarkMain - INFO - ===== Run 1/243: Testing with settings: {'OMP_NUM_THREADS': 1, 'OPENBLAS_NUM_THREADS': 1, 'MKL_NUM_THREADS': 1, 'VECLIB_MAXIMUM_THREADS': 1, 'NUMEXPR_NUM_THREADS': 1} =====
2025-06-13 15:44:51,690 - Benchm

KeyboardInterrupt: 

In [ ]:
# import qiskit
# import sys
# import os
#
# print(f"Qiskit Version: {qiskit.__version__}")
# print(f"Python Version: {sys.version}")
# print(f"Python Executable: {sys.executable}")
# print(f"Current Working Directory: {os.getcwd()}")
#
# # Attempt to import some common Qiskit elements to see which paths work
# try:
#     from qiskit.algorithms.minimum_eigensolvers import QAOA
#     print("from qiskit.algorithms.minimum_eigensolvers import QAOA -> SUCCESS")
# except ImportError:
#     print("from qiskit.algorithms.minimum_eigensolvers import QAOA -> FAILED")
#
# try:
#     from qiskit.algorithms.optimizers import COBYLA
#     print("from qiskit.algorithms.optimizers import COBYLA -> SUCCESS")
# except ImportError:
#     print("from qiskit.algorithms.optimizers import COBYLA -> FAILED")
#
# try:
#     from qiskit.utils import algorithm_globals
#     print("from qiskit.utils import algorithm_globals -> SUCCESS")
# except ImportError:
#     print("from qiskit.utils import algorithm_globals -> FAILED")
#
# try:
#     from qiskit_optimization.problems import QuadraticProgram
#     print("from qiskit_optimization.problems import QuadraticProgram -> SUCCESS")
# except ImportError:
#     print("from qiskit_optimization.problems import QuadraticProgram -> FAILED")
#
# try:
#     from qiskit_optimization.algorithms import MinimumEigenOptimizer
#     print("from qiskit_optimization.algorithms import MinimumEigenOptimizer -> SUCCESS")
# except ImportError:
#     print("from qiskit_optimization.algorithms import MinimumEigenOptimizer -> FAILED")
#
# try:
#     from qiskit_optimization.converters import QuadraticProgramToQubo
#     print("from qiskit_optimization.converters import QuadraticProgramToQubo -> SUCCESS")
# except ImportError:
#     print("from qiskit_optimization.converters import QuadraticProgramToQubo -> FAILED")

In [ ]:


# NEW CELL: Plotting Benchmarking Results

print("\n### Plotting Benchmarking Results ###")

# Create a string label for each combination for x-axis
df_results['combo_label'] = df_results.apply(
    lambda row: (f"O:{row['OMP_NUM_THREADS']}-"
                 f"B:{row['OPENBLAS_NUM_THREADS']}-"
                 f"M:{row['MKL_NUM_THREADS']}-"
                 f"V:{row['VECLIB_MAXIMUM_THREADS']}-"
                 f"N:{row['NUMEXPR_NUM_THREADS']}"),
    axis=1
)

# --- Plotting Average Execute Time per Cost Function Call ---
plt.figure(figsize=(18, 8)) # Increased figure size for more labels
plt.bar(df_results['combo_label'], df_results['avg_execute_time'], color='skyblue')
plt.xlabel('Environment Variable Combinations')
plt.ylabel('Average Execute Time per Cost Function Call (s)')
plt.title(f'Average Execute Time for N={N}, p={p} Across Environment Combinations')
plt.xticks(rotation=90, fontsize=8) # Rotate labels for readability
plt.grid(axis='y', linestyle='--', alpha=0.7)
plt.tight_layout() # Adjust layout to prevent labels from overlapping
plt.show()

# --- Plotting Total Overall Optimization Duration ---
plt.figure(figsize=(18, 8)) # Increased figure size
plt.bar(df_results['combo_label'], df_results['total_overall_duration'], color='lightcoral')
plt.xlabel('Environment Variable Combinations')
plt.ylabel('Total Overall Duration (s)')
plt.title(f'Total Optimization Duration for N={N}, p={p} Across Environment Combinations')
plt.xticks(rotation=90, fontsize=8) # Rotate labels for readability
plt.grid(axis='y', linestyle='--', alpha=0.7)
plt.tight_layout() # Adjust layout
plt.show()

print("\n--- Plotting Tips ---")
print("If the bar charts are too crowded (e.g., for 243 combinations), consider these alternatives:")
print("1. **Filter Data:** Analyze subsets, e.g., only combinations where MKL_NUM_THREADS = 1.")
print("2. **Heatmaps:** If you vary only two main variables (e.g., OMP_NUM_THREADS and OPENBLAS_NUM_THREADS) and keep others fixed, a heatmap can be very effective.")
print("   Example (uncomment and adapt if needed for your filtered data):")
print("""
# import seaborn as sns
# df_filtered_for_heatmap = df_results[
#     (df_results['MKL_NUM_THREADS'] == 1) &
#     (df_results['VECLIB_MAXIMUM_THREADS'] == 1) &
#     (df_results['NUMEXPR_NUM_THREADS'] == 1)
# ]
# if not df_filtered_for_heatmap.empty:
#     pivot_table_avg_exec = df_filtered_for_heatmap.pivot_table(
#         index='OMP_NUM_THREADS', columns='OPENBLAS_NUM_THREADS', values='avg_execute_time'
#     )
#     plt.figure(figsize=(8, 6))
#     sns.heatmap(pivot_table_avg_exec, annot=True, cmap='viridis', fmt=".4f", cbar_kws={'label': 'Average Execute Time (s)'})
#     plt.title('Avg. Execute Time Heatmap (MKL, VECLIB, NUMEXPR = 1)')
#     plt.xlabel('OPENBLAS_NUM_THREADS')
#     plt.ylabel('OMP_NUM_THREADS')
#     plt.show()

#     pivot_table_total_dur = df_filtered_for_heatmap.pivot_table(
#         index='OMP_NUM_THREADS', columns='OPENBLAS_NUM_THREADS', values='total_overall_duration'
#     )
#     plt.figure(figsize=(8, 6))
#     sns.heatmap(pivot_table_total_dur, annot=True, cmap='magma', fmt=".2f", cbar_kws={'label': 'Total Duration (s)'})
#     plt.title('Total Duration Heatmap (MKL, VECLIB, NUMEXPR = 1)')
#     plt.xlabel('OPENBLAS_NUM_THREADS')
#     plt.ylabel('OMP_NUM_THREADS')
#     plt.show()
# else:
#     print("No data to plot heatmap for filtered subset (all MKL, VECLIB, NUMEXPR == 1).")
""")

## 5. Optional: Analyze the Best Optimal Bitstring

This section remains the same, but it will only process the result from the *last* benchmark run if you keep the `best_overall_params` variable as-is.

In [ ]:
# In Jupyter Notebook, Cell 10 (Optional: Analyze the Best Optimal Bitstring)

# Ensure df_results exists and is not empty
if 'df_results' in locals() and not df_results.empty:
    print("\n" + "---" * 20)
    print("### Analyzing the OVERALL Best Result for Optimal Bitstring ###")

    # Find the row with the minimum optimal_energy from all benchmark runs
    best_row = df_results.loc[df_results['optimal_energy'].idxmin()]

    best_overall_params = best_row['optimal_params']
    best_energy = best_row['optimal_energy']
    best_nfev = best_row['nfev']
    best_runtime = best_row['optimizer_runtime']
    best_env_settings = {k: best_row[k] for k in ["OMP_NUM_THREADS", "OPENBLAS_NUM_THREADS", "MKL_NUM_THREADS", "VECLIB_MAXIMUM_THREADS", "NUMEXPR_NUM_THREADS"]}


    print(f"Overall Best Energy: {best_energy:.6f}")
    print(f"Optimal Parameters from Best Run: {np.array(best_overall_params)[:2].round(3)}...") # Print first two params
    print(f"NFEV: {best_nfev}, Optimizer Runtime: {best_runtime:.2f}s")
    print(f"Environment settings for Best Run: {best_env_settings}")
    print("--------------------------------------------------------------------------------")


    optimal_parameters = np.array(best_overall_params)
    print(f"\nUsing optimal parameters from the overall best run: {optimal_parameters[:2].round(3)}...")

    # --- Extracting the Optimal Bitstring (Measurement) ---

    gamma_opt = ParameterVector('gamma', p)
    beta_opt = ParameterVector('beta', p)

    # Recreate the optimal circuit structure with ParameterVectors
    optimal_circuit = get_parameterized_qaoa_circuit(
        po_problem=po_problem,
        depth=p,
        ini_type='dicke',
        mixer_type='trotter_ring',
        T=1,
        simulator=None, # Use the Sampler directly for measurement
        mixer_topology='linear',
        gamma=gamma_opt,
        beta=beta_opt
    )
    # Bind the optimal parameters to the circuit
    optimal_circuit_bound = optimal_circuit.assign_parameters({
        gamma_opt: optimal_parameters[:p],
        beta_opt: optimal_parameters[p:]
    })

    # Add measurements for sampling
    optimal_circuit_bound.measure_all()

    sampler_shots = 1024 # Use more shots for better statistical sampling of the optimal bitstring

    sampler = Sampler()

    print(f"\n--- Sampling for Optimal Bitstring ({sampler_shots} shots) ---")
    sampler_job = sampler.run(optimal_circuit_bound, shots=sampler_shots)
    sampler_result = sampler_job.result()

    # Use binary_probabilities for direct access to probabilities
    counts = sampler_result.quasi_dists[0].binary_probabilities()

    sorted_counts = sorted(counts.items(), key=lambda item: item[1], reverse=True)

    print("Top 5 most frequent bitstrings and their probabilities:")
    optimal_bitstring = None
    for i, (bitstring, probability) in enumerate(sorted_counts[:5]):
        print(f"  {bitstring}: {probability:.4f}")
        if i == 0:
            optimal_bitstring = bitstring

    if optimal_bitstring:
        optimal_selection = np.array([int(b) for b in optimal_bitstring])
        selected_assets_count = np.sum(optimal_selection)

        print(f"\nMost probable portfolio selection (bitstring): {optimal_bitstring}")
        print(f"Number of selected assets: {selected_assets_count} (Expected K={K})")

        # Function to evaluate the classical objective energy for a given bitstring
        # This is the original problem cost, not the DWE-modified QUBO energy
        def evaluate_bitstring_original_cost(bitstring_array, original_mu, original_Sigma, original_q):
            x = bitstring_array
            portfolio_variance = np.dot(x, np.dot(original_Sigma, x))
            portfolio_return = np.dot(original_mu, x)
            return original_q * portfolio_variance - portfolio_return

        optimal_classical_energy_for_bitstring = evaluate_bitstring_original_cost(
            optimal_selection,
            po_problem['means'],
            po_problem['cov'],
            po_problem['q_orig']
        )
        print(f"Classical objective energy for the most probable bitstring (original cost): {optimal_classical_energy_for_bitstring:.6f}")
        print(f"Number of assets selected by most probable bitstring: {np.sum(optimal_selection)}")
    else:
        print("Could not determine optimal bitstring.")
else:
    print("Cannot analyze optimal bitstring: 'df_results' DataFrame is not available or is empty. Please run the benchmarking cell first and ensure it completes successfully.")

# forget about the above

In [ ]:
import qokit
import inspect
import sys

# Removed the line that caused the AttributeError
# print(f"QOKit version: {qokit.__version__}")

try:
    print(f"QOKit installed at: {qokit.__file__}\n")
except AttributeError:
    print("Could not determine QOKit installation path via __file__ (unusual, might be a namespace package).\n")
    print("Attempting to search in common site-packages paths for QOKit.")
    # Fallback for highly unusual setups, though __file__ usually works for packages
    for path in sys.path:
        if 'qokit' in path.lower() and 'site-packages' in path.lower():
            print(f"Potential QOKit root in site-packages: {path}")
            break


# List of common places this function might be in QOKit
possible_modules = [
    'qokit.portfolio_optimization',
    'qokit.qaoa_portfolio_optimization', # Common in newer QOKit
    'qokit.problems.qaoa_portfolio_optimization_problem', # Another possible path
    'qokit.qaoa_circuit_portfolio', # Less likely for objective, but worth a check
    # Add other paths here if you suspect them from your project structure
]

found_path = None
print("Searching for 'get_qaoa_portfolio_objective_and_executor' in common QOKit modules:")
for module_path in possible_modules:
    try:
        # Dynamically import the module
        module = __import__(module_path, fromlist=['get_qaoa_portfolio_objective_and_executor'])

        # Check if the function exists in the imported module
        if hasattr(module, 'get_qaoa_portfolio_objective_and_executor'):
            print(f"  SUCCESS: 'get_qaoa_portfolio_objective_and_executor' found in: {module_path}")
            found_path = module_path
            break # Stop once found
        else:
            print(f"  Checked '{module_path}' - function not found there.")
    except ImportError:
        # This module path simply doesn't exist in the installed QOKit
        print(f"  Module '{module_path}' could not be imported.")
    except Exception as e:
        # Catch any other unexpected errors during import/attribute access
        print(f"  An unexpected error occurred while checking '{module_path}': {type(e).__name__}: {e}")

if found_path:
    print(f"\n--- Confirmed Import Path ---")
    print(f"Please use this exact import statement in your 'qaoa_helpers.py' file:")
    print(f"from {found_path} import get_qaoa_portfolio_objective_and_executor")
    print("-----------------------------\n")
else:
    print("\n--- Diagnostic Result ---")
    print("Could not find 'get_qaoa_portfolio_objective_and_executor' in common QOKit paths.")
    print("This is unexpected if you've been using it. It might be: ")
    print("1. In a very unusual QOKit location/version.")
    print("2. Named differently in your specific setup.")
    print("3. Shadowed by a local file (ensure you don't have similarly named .py files in your working directory that are not part of the QOKit installation).")
    print("---------------------------\n")

In [ ]:
import os
import subprocess
import itertools
import json
import time
import pandas as pd # For easy CSV export

# Define the environment variables and their values to test
env_vars_to_test = {
    "OMP_NUM_THREADS": [1, 4, 8],
    "OPENBLAS_NUM_THREADS": [1, 4, 8],
    "MKL_NUM_THREADS": [1, 4, 8],
    "VECLIB_MAXIMUM_THREADS": [1, 4, 8],
    "NUMEXPR_NUM_THREADS": [1, 4, 8],
}

# Path to the QAOA execution script
# Ensure 'run_qaoa_test.py' is in the same directory as this notebook
qaoa_script_path = "run_qaoa_test.py"

In [ ]:
all_benchmark_results = []
keys = list(env_vars_to_test.keys())
values_list = list(env_vars_to_test.values())
all_combinations = list(itertools.product(*values_list))
total_configs = len(all_combinations)

print(f"Starting {total_configs} benchmark configurations...")
print(f"Make sure '{qaoa_script_path}' and 'qaoa_helpers.py' are in the same directory.")

start_benchmarking_overall_time = time.perf_counter()

for i, combo in enumerate(all_combinations):
    env_settings = dict(zip(keys, combo))
    print(f"\n--- Running configuration {i+1}/{total_configs}: {env_settings} ---")

    # Prepare environment for the subprocess
    current_env = os.environ.copy()
    for var, value in env_settings.items():
        current_env[var] = str(value) # Environment variables must be strings

    try:
        # Execute run_qaoa_test.py as a subprocess
        # It prints its results as a JSON object to stdout
        process = subprocess.run(
            ["python", qaoa_script_path],
            env=current_env,
            capture_output=True,
            text=True, # Decode stdout/stderr as text
            check=True # Raise CalledProcessError for non-zero exit codes (script errors)
        )
        # Parse the JSON output from the subprocess
        benchmark_output = json.loads(process.stdout.strip())
        all_benchmark_results.append(benchmark_output)
        print(f"  Completed in {benchmark_output.get('overall_duration_seconds', 'N/A'):.2f}s, Energy: {benchmark_output.get('best_overall_energy', 'N/A'):.6f}")

    except subprocess.CalledProcessError as e:
        print(f"  ERROR: Benchmark FAILED for settings {env_settings}")
        print(f"  Stdout:\n{e.stdout}")
        print(f"  Stderr:\n{e.stderr}")
        error_result = {"error": str(e), "env_settings": env_settings, "run_status": "FAILED"}
        # Add a placeholder for duration to ensure it doesn't break later steps if needed
        error_result["overall_duration_seconds"] = float('inf') # Mark as very long
        all_benchmark_results.append(error_result)
    except json.JSONDecodeError as e:
        print(f"  ERROR: JSON decode error for settings {env_settings}: {e}")
        print(f"  Raw stdout:\n{process.stdout}") # Print raw stdout for debugging JSON issues
        error_result = {"error": f"JSON decode error: {e}", "env_settings": env_settings, "run_status": "FAILED"}
        error_result["overall_duration_seconds"] = float('inf')
        all_benchmark_results.append(error_result)
    except Exception as e:
        print(f"  ERROR: An unexpected error occurred for settings {env_settings}: {e}")
        error_result = {"error": str(e), "env_settings": env_settings, "run_status": "FAILED"}
        error_result["overall_duration_seconds"] = float('inf')
        all_benchmark_results.append(error_result)

end_benchmarking_overall_time = time.perf_counter()
total_benchmark_duration = end_benchmarking_overall_time - start_benchmarking_overall_time
print(f"\nAll benchmarking runs completed in {total_benchmark_duration:.2f} seconds.")